In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Osteoporosis"
cohort = "GSE56815"

# Input paths
in_trait_dir = "../../input/GEO/Osteoporosis"
in_cohort_dir = "../../input/GEO/Osteoporosis/GSE56815"

# Output paths
out_data_file = "../../output/preprocess/Osteoporosis/GSE56815.csv"
out_gene_data_file = "../../output/preprocess/Osteoporosis/gene_data/GSE56815.csv"
out_clinical_data_file = "../../output/preprocess/Osteoporosis/clinical_data/GSE56815.csv"
json_path = "../../output/preprocess/Osteoporosis/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"Gene expression study of blood monocytes in pre- and postmenopausal females with low or high bone mineral density (HG-U133A)"
!Series_summary	"Comparison of circulating monocytes from pre- and postmanopausal females with low or high bone mineral density (BMD). Circulating monocytes are progenitors of osteoclasts, and produce factors important to bone metabolism. Results provide insight into the role of monocytes in osteoporosis."
!Series_summary	"We identify osteoporosis genes by microarray analyses of monocytes in high vs. low hip BMD (bone mineral density) subjects."
!Series_overall_design	"Microarray analyses of monocytes were performed using Affymetrix HG-133A arrays in 80 Caucasian females, including 40 high (20 pre- and 20 postmanopausal) and 40 low hip BMD (20 pre- and 20 postmanopausal) subjects"
Sample Characteristics Dictionary:
{0: ['gender: Female'], 1: ['bone mineral density: high BMD', 'bone mineral density: low BMD'], 2: ['state: po

### Step 2: Dataset Analysis and Clinical Feature Extraction

In [3]:
# 1. Gene Expression Data Assessment
# Based on the background information, this dataset appears to contain gene expression data 
# from Affymetrix HG-133A arrays
is_gene_available = True

# 2. Variable Availability and Data Type Conversion
# 2.1 Data Availability

# For trait data: osteoporosis can be inferred from BMD (bone mineral density) data
trait_row = 1  # 'bone mineral density' is in the row index 1

# Age-related data not available directly, but menopausal state can be used as a proxy for age ranges
# However, menopausal state is categorical, not continuous age
age_row = 2  # 'state' (menopausal status) is in row index 2

# Gender data is available but seems constant (all Female)
gender_row = None  # All subjects are female so this is a constant feature

# 2.2 Data Type Conversion Functions

def convert_trait(value):
    """Convert bone mineral density data to binary trait values for osteoporosis."""
    if pd.isna(value) or value is None:
        return None
    
    # Extract the value part after the colon if present
    if isinstance(value, str) and ':' in value:
        value = value.split(':', 1)[1].strip()
    
    # Low BMD indicates osteoporosis, high BMD indicates normal/healthy
    if 'low' in value.lower():
        return 1  # Osteoporosis (condition present)
    elif 'high' in value.lower():
        return 0  # Normal/healthy (condition absent)
    else:
        return None

def convert_age(value):
    """Convert menopausal state to a binary age-related variable."""
    if pd.isna(value) or value is None:
        return None
    
    # Extract the value part after the colon if present
    if isinstance(value, str) and ':' in value:
        value = value.split(':', 1)[1].strip()
    
    # Postmenopausal women are typically older (>50 years), premenopausal are younger
    if 'post' in value.lower():
        return 1  # Postmenopausal (older)
    elif 'pre' in value.lower():
        return 0  # Premenopausal (younger)
    else:
        return None

def convert_gender(value):
    """Convert gender data to binary, though not needed as all subjects are female."""
    if pd.isna(value) or value is None:
        return None
    
    # Extract the value part after the colon if present
    if isinstance(value, str) and ':' in value:
        value = value.split(':', 1)[1].strip()
    
    # Standard conversion: female=0, male=1
    if value.lower() == 'female':
        return 0
    elif value.lower() == 'male':
        return 1
    else:
        return None

# 3. Save Metadata - Initial filtering based on data availability
is_trait_available = trait_row is not None
validate_and_save_cohort_info(
    is_final=False,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# 4. Clinical Feature Extraction
if trait_row is not None:
    # Extract clinical features using the library function
    selected_clinical_df = geo_select_clinical_features(
        clinical_df=clinical_data,
        trait=trait,
        trait_row=trait_row,
        convert_trait=convert_trait,
        age_row=age_row,
        convert_age=convert_age,
        gender_row=None,  # All subjects are female, so gender is constant
        convert_gender=None
    )
    
    # Preview the extracted clinical data
    print("Preview of selected clinical features:")
    print(preview_df(selected_clinical_df))
    
    # Save the clinical data to CSV
    os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
    selected_clinical_df.to_csv(out_clinical_data_file, index=True)
    print(f"Clinical data saved to {out_clinical_data_file}")


Preview of selected clinical features:
{'GSM1369756': [0.0, 1.0], 'GSM1369757': [0.0, 1.0], 'GSM1369758': [0.0, 1.0], 'GSM1369759': [0.0, 1.0], 'GSM1369760': [0.0, 1.0], 'GSM1369761': [0.0, 1.0], 'GSM1369762': [0.0, 1.0], 'GSM1369763': [0.0, 0.0], 'GSM1369764': [0.0, 0.0], 'GSM1369765': [0.0, 1.0], 'GSM1369766': [0.0, 0.0], 'GSM1369767': [0.0, 1.0], 'GSM1369768': [0.0, 0.0], 'GSM1369769': [0.0, 1.0], 'GSM1369770': [0.0, 0.0], 'GSM1369771': [0.0, 1.0], 'GSM1369772': [0.0, 0.0], 'GSM1369773': [0.0, 0.0], 'GSM1369774': [0.0, 0.0], 'GSM1369775': [0.0, 0.0], 'GSM1369776': [0.0, 0.0], 'GSM1369777': [0.0, 1.0], 'GSM1369778': [0.0, 1.0], 'GSM1369779': [0.0, 1.0], 'GSM1369780': [0.0, 1.0], 'GSM1369781': [0.0, 1.0], 'GSM1369782': [0.0, 1.0], 'GSM1369783': [0.0, 1.0], 'GSM1369784': [0.0, 1.0], 'GSM1369785': [0.0, 0.0], 'GSM1369786': [0.0, 0.0], 'GSM1369787': [0.0, 0.0], 'GSM1369788': [0.0, 0.0], 'GSM1369789': [0.0, 0.0], 'GSM1369790': [0.0, 0.0], 'GSM1369791': [0.0, 0.0], 'GSM1369792': [0.0, 1.0]

### Step 3: Gene Data Extraction

In [4]:
# 1. Use the get_genetic_data function from the library to get the gene_data from the matrix_file previously defined.
gene_data = get_genetic_data(matrix_file)

# 2. Print the first 20 row IDs (gene or probe identifiers) for future observation.
print(gene_data.index[:20])


Index(['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at', '1294_at',
       '1316_at', '1320_at', '1405_i_at', '1431_at', '1438_at', '1487_at',
       '1494_f_at', '1598_g_at', '160020_at', '1729_at', '1773_at', '177_at',
       '179_at', '1861_at'],
      dtype='object', name='ID')


### Step 4: Gene Identifier Review

In [5]:
# These identifiers appear to be Affymetrix microarray probe IDs, not standard human gene symbols.
# For example, "1007_s_at", "1053_at" are in a format typical of Affymetrix arrays.
# They will need to be mapped to human gene symbols for biological interpretation.

requires_gene_mapping = True


### Step 5: Gene Annotation

In [6]:
# 1. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 2. Use the 'preview_df' function from the library to preview the data and print out the results.
print("Gene annotation preview:")
print(preview_df(gene_annotation))


Gene annotation preview:
{'ID': ['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at'], 'GB_ACC': ['U48705', 'M87338', 'X51757', 'X69699', 'L36861'], 'SPOT_ID': [nan, nan, nan, nan, nan], 'Species Scientific Name': ['Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens'], 'Annotation Date': ['Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014'], 'Sequence Type': ['Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence'], 'Sequence Source': ['Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database'], 'Target Description': ['U48705 /FEATURE=mRNA /DEFINITION=HSU48705 Human receptor tyrosine kinase DDR gene, complete cds', 'M87338 /FEATURE= /DEFINITION=HUMA1SBU Human replication factor C, 40-kDa subunit (A1) mRNA, complete cds', "X51757 /FEATURE=cds /DEFINITION=HSP70B Human heat-shock protein HSP70B' gene", 'X69699 /FEATURE= /DEF

### Step 6: Gene Identifier Mapping

In [7]:
# 1. Identify the keys for gene identifiers and gene symbols
# From the gene expression data, the identifiers are formatted like "1007_s_at", which appear to match
# the 'ID' column in the gene annotation dataframe

# From the gene annotation preview, we see the 'Gene Symbol' column contains standard human gene symbols
# like "DDR1 /// MIR4640", "RFC2", etc.

# 2. Create gene mapping dataframe
gene_mapping = get_gene_mapping(gene_annotation, prob_col='ID', gene_col='Gene Symbol')

# 3. Apply gene mapping to convert probe-level measurements to gene expression data
gene_data = apply_gene_mapping(gene_data, gene_mapping)

# Preview the first few rows of the mapped gene expression data
print("Preview of gene data after mapping:")
print(gene_data.index[:10])
print(f"Shape of gene expression data: {gene_data.shape}")


Preview of gene data after mapping:
Index(['A1CF', 'A2M', 'A4GALT', 'A4GNT', 'AAAS', 'AACS', 'AADAC', 'AAGAB',
       'AAK1', 'AAMDC'],
      dtype='object', name='Gene')
Shape of gene expression data: (13830, 80)


### Step 7: Data Normalization and Linking

In [8]:
# 1. Normalize the obtained gene data with the 'normalize_gene_symbols_in_index' function from the library.
normalized_gene_data = normalize_gene_symbols_in_index(gene_data)
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
normalized_gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene data saved to {out_gene_data_file}")

# Create clinical features directly from clinical_data using the conversion functions defined earlier
clinical_features_df = geo_select_clinical_features(
    clinical_data, 
    trait=trait, 
    trait_row=trait_row, 
    convert_trait=convert_trait,
    age_row=age_row,
    convert_age=convert_age,
    gender_row=gender_row,
    convert_gender=convert_gender
)

# Save the clinical data
os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
clinical_features_df.to_csv(out_clinical_data_file)
print(f"Clinical data saved to {out_clinical_data_file}")

# Now link the clinical and genetic data
linked_data = geo_link_clinical_genetic_data(clinical_features_df, normalized_gene_data)
print("Linked data shape:", linked_data.shape)

# Handle missing values in the linked data
linked_data = handle_missing_values(linked_data, trait)

# 4. Determine whether the trait and some demographic features are severely biased, and remove biased features.
is_trait_biased, unbiased_linked_data = judge_and_remove_biased_features(linked_data, trait)

# 5. Conduct quality check and save the cohort information.
is_usable = validate_and_save_cohort_info(
    is_final=True, 
    cohort=cohort, 
    info_path=json_path, 
    is_gene_available=True, 
    is_trait_available=True, 
    is_biased=is_trait_biased, 
    df=unbiased_linked_data,
    note="This is an HPV-transformed keratinocyte cell line study focusing on transformation stages: 1 for anchorage independent (more advanced cancer stage), 0 for earlier stages."
)

# 6. If the linked data is usable, save it as a CSV file to 'out_data_file'.
if is_usable:
    os.makedirs(os.path.dirname(out_data_file), exist_ok=True)
    unbiased_linked_data.to_csv(out_data_file)
    print(f"Linked data saved to {out_data_file}")
else:
    print("Data was determined to be unusable and was not saved")

Normalized gene data saved to ../../output/preprocess/Osteoporosis/gene_data/GSE56815.csv
Clinical data saved to ../../output/preprocess/Osteoporosis/clinical_data/GSE56815.csv
Linked data shape: (80, 13544)


For the feature 'Osteoporosis', the least common label is '0.0' with 40 occurrences. This represents 50.00% of the dataset.
The distribution of the feature 'Osteoporosis' in this dataset is fine.

Quartiles for 'Age':
  25%: 0.0
  50% (Median): 0.5
  75%: 1.0
Min: 0.0
Max: 1.0
The distribution of the feature 'Age' in this dataset is fine.



Linked data saved to ../../output/preprocess/Osteoporosis/GSE56815.csv
